In [35]:
from notepad import WaterStorage

%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


Developments steps to take: 
* Test the WaterStorage
* Create some example for WaterStorage
* Define interactions WaterStorage <> Heatpump
* Create some example for WaterStorage + Heatpump
* Develop the interactions --> Create working examples

## WaterStorage

Functional requirements for the WaterStorage:
* Given:      
    * Size / capacity
    * Temperature in/out
    * Max power
    * Roundtripp efficiency
* It should be able to execute commands, like: 
    * Charge
    * Discharge
    * Whats the storage level? 
    * Assign financials    
    * Take into account storage losses (time dependent)

In [36]:
waterstorage = WaterStorage(
    name='MyStorage',
    max_power=10,
    min_power=-10,
    roundtrip_eff=0.90,
    energy_density = 50 * 10e-3,
    volume = 500,
    lifetime = 25,
    temperature = 368, #K
    min_storagelevel = 5,
    max_storagelevel = 23
    
)

In [37]:
waterstorage.set_freq('15T')

In [38]:
waterstorage.set_storagelevel(15)
waterstorage.storagelevel

15

In [39]:
waterstorage.charging_power_limit

32.0

In [40]:
waterstorage.charge(100)

32.0

In [41]:
waterstorage.storagelevel

23

In [42]:
waterstorage.charge(100)

0.0

In [43]:
waterstorage.discharge(50)

50.0

In [ ]:
def test_heatpump_and_waterstorage_system(Tsink, Tsource, process_demand_MW, e_price, waterstorage_level):
    """
    1. Follow a certain logic based on given price:
        - If price is low --> Heatpump at full power, and charge the heatbuffer
        - If price is high --> Discharge the heat buffer, and increase Tsource, which will increase COP
    2. Above logic should adhere to a couple of constraints:
        - Storage levels
        - Capacity of the heat pump 
        - Process demand
        - ....
    3. This function should contain: 
        - Heat pump 
        - Water storage
        - Interactions / logic between them
    4. Output of the function:
        - Power of the heatpump 
        - "New" water storage level
    """
    waterstorage.storage_level = waterstorage_level
    
    if price > 100:
        hp_load = heatpump.set_load('max')
        energy_to_storage = hp_load - demand
        waterstorage.charge(energy_to_storage)
        waterstorage_level = waterstorage.storage_level
    if price < 50:
        energy_from_storage = waterstorage.discharge('max')
        waterstorage_level = waterstorage.storage_level
        new_Tsource = Tsource_calc(Tsource, energy_from_storage)
        new_COP = cop_calc(new_Tsource, Tsink) 
        hp_load = heatpump.set_load(demand, new_COP)
    return hp_load, waterstorage_level
    
hp_load, waterstorage_level = test_heatpump_waterstorage_system(
    Tsink = 373+100, 
    Tsoucre = 373+50, 
    process_demand = 20, 
    e_price = 150, 
    waterstorage_level = 0.50
)

# Expected behaviour: 
    # hp_heat_output == demand
    # hp source temparture > than before
    # waterstorage_level < than before
    # hp cop > higher than before
hp_load, waterstorage_level

In [44]:
Tsink = 413 #K
Tsource = 333 #K
Tref = 273 #K
hp_capacity = 31 #MW
demand = 25 #MW
Cp = 4190  #J/kgK
MW_to_J_per_s = 1000_000
hp_capacity *= MW_to_J_per_s
demand *= MW_to_J_per_s

In [45]:
def hp_mass_flow (hp_capacity, Tsink, Tref, Cp):
    return hp_capacity /(Cp*(Tsink - Tref)) 
hp_mass_flow (31_000_000, 413, 273, 4190)

52.84691442209342

In [46]:
def process_mass_flow (demand, Tsink, Tref, Cp):
    return demand /(Cp*(Tsink - Tref)) 
process_mass_flow (25_000_000, 413, 273, 4190)

42.61847937265598

In [47]:
charge_mass_flow = 52 - 42 #can be written as a functiality
charged_heat = (charge_mass_flow * Cp * (Tsink - Tref)) / MW_to_J_per_s
charged_heat

5.866

In [48]:
# charge_mass_flow = 52 - 42 #should be written as function
# def charge_heat (charge_mass_flow, Cp, Tsink, Tref, MW_to_J_per_s):
#     return (charge_mass_flow * Cp * (Tsink - Tref)) / MW_to_J_per_s
# charge_heat (10, 4190, 413, 273, 1000_000)

In [49]:
# def source_mass_flow (demand, Tsource, Tref, Cp):
#     return demand /(Cp*(Tsource - Tref)) 
# source_mass_flow (25_000_000, 333, 273, 4190) 

In [50]:
# efficiency = 0.7
Tstorage = 95 + 273
discharge_mass_flow = charge_mass_flow
discharged_heat = (discharge_mass_flow * Cp * (Tsource - Tref)) / MW_to_J_per_s
discharged_heat
# mass flows need to be balanced not energy
#This energy loss is because storage is charged with high temperature and discharged with low.
# heat loss can be neglected assuming that storage is well-insulated.

2.514

In [56]:
# Tsource_new = (discharge_mass_flow * T_discharge + Tsource * source_mass_flow) / (discharge_mass_flow + source_mass_flow)
Tsource_new = (10 * 95 + 60*42) / (10+42)
Tsource_new


66.73076923076923

In [57]:
Tsource_new +=273
COP_new = Tsink / (Tsink - Tsource_new)
COP_new

5.636745406824146

In [53]:
waterstorage.__dict__.keys()

dict_keys(['name', 'id', 'max_power', 'min_power', 'modes', 'roundtrip_eff', 'volume', 'lifetime', 'temperature', 'energy_density', 'max_storage_capacity', 'max_storagelevel', 'min_storagelevel', 'freq', 'time_factor', 'storagelevel'])

In [128]:
# max_storage_capacity is in MWh and it should inherit MWh to MW conversion from Assets
#  MW = MWh / self.time_factor
waterstorage.max_storage_capacity

23.2

In [129]:
# chargelevel = self.chargelevel
# max_charging = chargelevel - self.max_chargelevel
# max_discharging = chargelevel - self.min_chargelevel

In [130]:
# Funtionality: Set the storage level
waterstorage.storagelevel = 15
waterstorage.max_storagelevel = 23.2
waterstorage.min_storagelevel = 5
# waterstorage.max_charging = waterstorage.max_storagelevel - waterstorage.storagelevel
# waterstorage.max_discharging = waterstorage.max_storagelevel - waterstorage.min_storagelevel
waterstorage.max_discharging

18.2

In [131]:
# Functionality: Charge the storage
waterstorage.storage_level = 15
waterstorage.charge = 5
waterstorage.storage_level += waterstorage.charge
waterstorage.storage_level

20

In [132]:
# Functionality: Discharge the storage
waterstorage.storage_level = 15
waterstorage.discharge = 4
waterstorage.storage_level -= waterstorage.discharge
waterstorage.storage_level

11

## WaterStorage + Heatpump system

Functional requirements for the WaterStorage + Heatpump system:
1. Goal (Funtional requirements): 
    * Given (context)
    * price (forecast), 
    * source and sink temperature (provided by process), 
    * process heat demand, 
    * storage level of the water storage (temperature level)
* I want to know:
    * Heat output from the heatpump (in MW)
    * New storage level / temperature level
    * Electricity consumption of the heatpump